# Reviews Text Sentiment Analysis For Thailand Tourism Recommendation

This project target for create recommendation system from rating thailand tourism by learning review positive or negative

#### Step #1 - Setup Project Library Package

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import sklearn as sk
import os
from geopy.geocoders import Nominatim
from dotenv import load_dotenv

load_dotenv()

True

#### Step #2 - Data Preparation
##### 2.1 Thailand Province -> Amphure Data <br>
https://github.com/kongvut/thai-province-data

In [2]:
province_data = pd.read_json('../hook/data/api_province_with_amphure_tambon.json')

In [3]:
central_province_data = province_data[province_data['geography_id'] != 2]
central_province_data.head(5)

id     name_th       name_en  geography_id                created_at  \
10  11      ชลบุรี     Chon Buri             5 2019-08-09 03:33:09+07:00   
11  12       ระยอง        Rayong             5 2019-08-09 03:33:09+07:00   
12  13    จันทบุรี   Chanthaburi             5 2019-08-09 03:33:09+07:00   
13  14        ตราด          Trat             5 2019-08-09 03:33:09+07:00   
14  15  ฉะเชิงเทรา  Chachoengsao             5 2019-08-09 03:33:09+07:00   

                  updated_at deleted_at  \
10 2022-05-16 06:31:03+07:00        NaT   
11 2022-05-16 06:31:03+07:00        NaT   
12 2022-05-16 06:31:03+07:00        NaT   
13 2022-05-16 06:31:03+07:00        NaT   
14 2022-05-16 06:31:03+07:00        NaT   

                                              amphure  
10  [{'id': 2001, 'name_th': 'เมืองชลบุรี', 'name_...  
11  [{'id': 2101, 'name_th': 'เมืองระยอง', 'name_e...  
12  [{'id': 2201, 'name_th': 'เมืองจันทบุรี', 'nam...  
13  [{'id': 2301, 'name_th': 'เมืองตราด', 'name_en...  
14  [{'id': 2401, 'name_th': 'เมืองฉะเชิงเทรา', 'n...

In [ ]:
# provinces = central_province_data['name_en'].tolist()
# geolocator = Nominatim(user_agent="thailand_provinces")
# data = {'Province': [], 'Latitude': [], 'Longitude': []}

# for province in provinces:
#     location = geolocator.geocode(f"{province}, Thailand")
#     if location:
#         data['Province'].append(province)
#         data['Latitude'].append(location.latitude)
#         data['Longitude'].append(location.longitude)

# thailland_province_coordinates = pd.DataFrame(data)


In [17]:
# thailland_province_coordinates = pd.read_csv("../dataset/locations/thailand_province_coordinate.csv", sep=',', encoding='utf-8')

In [26]:
import sys
import os

parent_directory = os.path.abspath(os.path.join(os.getcwd(), '..'))

sys.path.append(parent_directory)

sys.path.append(os.path.abspath(os.path.join(os.getcwd(), '../hook')))

 ##### 2.2 Thailand Tourism Location API Data <br>
https://developers.tourismthailand.org/

In [27]:
import hook.thai_tourism_data as tat
tourism_location = tat.ThaiTourismAPI("EN")

def getTourismLocationsByProvince(province_name, province_location, category):
    search_params = {
            "keyword": "",  # Example keyword for Kanchanaburi
            "location": province_location,
            "categorycodes": category,
            "province_name": province_name,
            "radius": 1000,
            "number_of_result": 100,
            "page_number": 1,
            "destination": province_name,
            "filter_by_update_date": "2018/01/01-2024/09/31"
        }
    tourism_data = tourism_location.fetch_search_location(**search_params)

    df = pd.DataFrame([vars(place) for place in tourism_data])
    return df


In [28]:
thailland_province_coordinates = pd.read_csv("../dataset/locations/thailand_province_coordinate.csv")

In [29]:
thailland_province_coordinates[['Province']]

Province
0                    Bangkok
1               Samut Prakan
2                 Nonthaburi
3               Pathum Thani
4   Phra Nakhon Si Ayutthaya
..                       ...
71               Phatthalung
72                   Pattani
73                      Yala
74                Narathiwat
75                 Bueng Kan

[76 rows x 1 columns]

In [30]:
tourism_attraction_locations = pd.DataFrame()
tourism_hotels_locations = pd.DataFrame()
tourism_restaurants_locations = pd.DataFrame()
tourism_shops_locations = pd.DataFrame()
# CATEGORIES: ATTRACTION | ACCOMMODATION  | RESTAURANT | GEOS | SHOP

for index, pvn in province_data.iterrows():
    coordinate = thailland_province_coordinates[thailland_province_coordinates['Province'] == pvn['name_en']]
    
    if len(coordinate['Latitude'].values) > 0:
        # tourism_shops_location = getTourismLocationsByProvince(pvn['name_th'], 
        # f"{coordinate['Latitude'].values[0]},"
        # f"{coordinate['Longitude'].values[0]}",
        # "SHOP")
        
        # tourism_shops_locations = pd.concat([tourism_shops_locations, tourism_shops_location], ignore_index=True)
        
        province_torism_location = getTourismLocationsByProvince(pvn['name_en'], 
        f"{coordinate['Latitude'].values[0]},"
        f"{coordinate['Longitude'].values[0]}",
        "ATTRACTION")
        
        tourism_attraction_locations = pd.concat([tourism_attraction_locations, province_torism_location], ignore_index=True)
        
        # tourism_hotels_location = getTourismLocationsByProvince(pvn['name_en'], 
        # f"{coordinate['Latitude'].values[0]},"
        # f"{coordinate['Longitude'].values[0]}",
        # "ACCOMMODATION")
        
        # tourism_hotels_locations = pd.concat([tourism_hotels_locations, tourism_hotels_location], ignore_index=True)
        
        # tourism_restaurants_location = getTourismLocationsByProvince(pvn['name_th'], 
        # f"{coordinate['Latitude'].values[0]},"
        # f"{coordinate['Longitude'].values[0]}",
        # "RESTAURANT")
        
        # tourism_restaurants_locations = pd.concat([tourism_restaurants_locations, tourism_restaurants_location], ignore_index=True)
        

In [12]:
tourism_shops_locations

Empty DataFrame
Columns: []
Index: []

In [22]:
tourism_attraction_locations

Empty DataFrame
Columns: []
Index: []

In [ ]:
tourism_hotels_locations

In [ ]:
tourism_restaurants_locations

In [12]:
# tourism_shops_locations.to_csv("tourism_shops_locations.csv", index=False, na_rep='N/A', header=True, sep=',', encoding='utf-8')

tourism_attraction_locations.to_csv("central_tourism_attraction_locations_en.csv", index=False, na_rep='N/A', header=True, sep=',', encoding='utf-8')

# tourism_hotels_locations.to_csv("tourism_hotels_locations.csv", index=False, na_rep='N/A', header=True, sep=',', encoding='utf-8')

# tourism_restaurants_locations.to_csv("tourism_restaurants_locations.csv", index=False, na_rep='N/A', header=True, sep=',', encoding='utf-8')

In [31]:
tourism_attraction_locations = pd.read_csv("../dataset/locations/tourism_attraction_locations_en.csv")
tourism_attraction_locations

place_id                           place_name   latitude   longitude  \
0     P03013220   Wat Ratchabophit Sathitmahasimaram  13.749132  100.497341   
1     P03013472                         Wat Yan Nawa  13.717333  100.513552   
2     P03013449                     Tiger God Shrine  13.753852  100.498319   
3     P03013827     Wat Thewarat Kunchorn Worawiharn  13.772303  100.501957   
4     P03013469            Wat Apson Sawan Worawihan  13.720030  100.469886   
...         ...                                  ...        ...         ...   
3636  P03017307                   Tham Fun Waterfall  18.266144  103.903480   
3637  P03012250                         Pu Ya Shrine  18.371745  103.649444   
3638  P03012246                        Kut Thing Yai  18.296982  103.662169   
3639  P03012247      Local Weaving Group Ban Sa Ngor  18.443938  103.416335   
3640  P03012248  The Northest Of Northeast Viewpoint  18.445139  103.410418   

     category_code category_description sha_name  sha_type_code  \
0       ATTRACTION           Attraction      NaN            NaN   
1       ATTRACTION           Attraction      NaN            NaN   
2       ATTRACTION           Attraction      NaN            NaN   
3       ATTRACTION           Attraction      NaN            NaN   
4       ATTRACTION           Attraction      NaN            NaN   
...            ...                  ...      ...            ...   
3636    ATTRACTION           Attraction      NaN            NaN   
3637    ATTRACTION           Attraction      NaN            NaN   
3638    ATTRACTION           Attraction      NaN            NaN   
3639    ATTRACTION           Attraction      NaN            NaN   
3640    ATTRACTION           Attraction      NaN            NaN   

     sha_type_description  sha_cate_id  ...                address  \
0                     NaN          NaN  ...   2 Fueang Nakhon Road   
1                     NaN          NaN  ...  40 Charoen Krung Road   
2                     NaN          NaN  ...         468 Tanao Road   
3                     NaN          NaN  ...                    NaN   
4                     NaN          NaN  ...                    NaN   
...                   ...          ...  ...                    ...   
3636                  NaN          NaN  ...                    NaN   
3637                  NaN          NaN  ...                    NaN   
3638                  NaN          NaN  ...                    NaN   
3639                  NaN          NaN  ...                    NaN   
3640                  NaN          NaN  ...                    NaN   

                  sub_district          district   province postcode  \
0             Wat Ratchabophit       Phra Nakhon    Bangkok  10200.0   
1                     Yan Nawa            Sathon    Bangkok  10120.0   
2             San Chaopho Suea       Phra Nakhon    Bangkok  10200.0   
3             Wachira Phayaban             Dusit    Bangkok  10300.0   
4     Pak Khlong Phasi Charoen     Phasi Charoen    Bangkok  10160.0   
...                        ...               ...        ...      ...   
3636                 Nong Doen         Bung Khla  Bueng Kan  38000.0   
3637                     Wisit  Mueang Bueng Kan  Bueng Kan  38000.0   
3638                Non Sombun  Mueang Bueng Kan  Bueng Kan  38000.0   
3639                   Ho Kham  Mueang Bueng Kan  Bueng Kan  38000.0   
3640                   Ho Kham  Mueang Bueng Kan  Bueng Kan  38000.0   

                                          thumbnail_url destination tags  \
0     https://tatapi.tourismthailand.org/tatfs/Image...     BANGKOK  NaN   
1     https://tatapi.tourismthailand.org/tatfs/Image...     BANGKOK  NaN   
2     https://tatapi.tourismthailand.org/tatfs/Image...     BANGKOK  NaN   
3     https://tatapi.tourismthailand.org/tatfs/Image...     BANGKOK  NaN   
4     https://tatapi.tourismthailand.org/tatfs/Image...     BANGKOK  NaN   
...                                                 ...         ...  ...   
3636  https://t

##### 2.3 TripAdvisor API Data <br>
https://tripadvisor-content-api.readme.io/reference/getlocationdetails

In [32]:
from hook.tripadvisor_data import TripAdvisorApi

load_dotenv()

# Ensure the API key is set
api_key = os.getenv('TRIPADVISOR_API_KEY')

# Initialize the API client
TripAdvisor_api = TripAdvisorApi(api_key, "EN")
# print(thai_tourism_api)

# Test API request
# response = thai_tourism_api.test_api_request()

In [33]:

response = TripAdvisor_api.location_search(
    "tk park",
    "attractions",
    None,
    "thailand",
    None,
    1000,
    "km",
    "en"
)
response.json()['data'][0]["location_id"]
location = response.json()['data']
# df_location = pd.concat(pd.DataFrame({"location_id": location['location_id'], "name": location['name']}))
# df_location

KeyError: 'data'

In [10]:
location

[{'location_id': '1997527',
  'name': 'TK Tour',
  'address_obj': {'city': 'Ko Samui',
   'state': 'Surat Thani Province',
   'country': 'Thailand',
   'postalcode': '84310',
   'address_string': '84310 Thailand'}}]

In [37]:

pd.DataFrame(pd.json_normalize(location))

location_id              name                   address_obj.street1  \
0    16735656  Address Sky View  Sheikh Mohammed Bin Rashed Boulevard   

  address_obj.city address_obj.state   address_obj.country  \
0            Dubai  Emirate of Dubai  United Arab Emirates   

                          address_obj.address_string  
0  Sheikh Mohammed Bin Rashed Boulevard, Dubai Un...

In [12]:
# tourism_attraction_locations
tripadvisor_central_attraction_locations = pd.DataFrame(columns=["location_id", "name", "province", "place_id"])

for index, attraction in central_tourism_attraction_locations.iterrows():

    response = TripAdvisor_api.location_search(
        attraction["place_name"],
        "attractions",
        None,
        "thailand",
        None,
        1000,
        "km",
        "en"
    )
    
    locations = response.json()['data']
    
    if len(locations) == 0:
        continue
    
    for sub_index, location in pd.DataFrame(pd.json_normalize(locations)).iterrows():
        
        print(f">>> #{index}/{sub_index} [$$$ {attraction['province']} | $$$ {attraction['place_id']}] {attraction['place_name']} ==> TripAdvisor [{location['name']}]")
        
        # Create a new DataFrame with the location_id and name
        new_entry = pd.DataFrame({
            "location_id": [location['location_id']], 
            "name": [location['name']],
            "province": attraction['province'],
            "place_id": attraction['place_id']
        })
        
        # Concatenate the new entry to the main DataFrame
        tripadvisor_central_attraction_locations = pd.concat([tripadvisor_central_attraction_locations, new_entry], ignore_index=True)
    
    # if index == 5:
    #     break

>>> #0/0 [$$$ Bangkok | $$$ P03013220] Wat Ratchabophit Sathitmahasimaram ==> TripAdvisor [Wat Ratchabophit]
>>> #0/1 [$$$ Bangkok | $$$ P03013220] Wat Ratchabophit Sathitmahasimaram ==> TripAdvisor [Wat Rajapradit Sathitmahasimaram Rajaworavihara]
>>> #0/2 [$$$ Bangkok | $$$ P03013220] Wat Ratchabophit Sathitmahasimaram ==> TripAdvisor [Wat Phra Chetuphon]
>>> #0/3 [$$$ Bangkok | $$$ P03013220] Wat Ratchabophit Sathitmahasimaram ==> TripAdvisor [Temple Of Dawn (Wat Arun)]
>>> #0/4 [$$$ Bangkok | $$$ P03013220] Wat Ratchabophit Sathitmahasimaram ==> TripAdvisor [Wat Umong]
>>> #0/5 [$$$ Bangkok | $$$ P03013220] Wat Ratchabophit Sathitmahasimaram ==> TripAdvisor [Wat Rong Khun]
>>> #0/6 [$$$ Bangkok | $$$ P03013220] Wat Ratchabophit Sathitmahasimaram ==> TripAdvisor [Wat Pak Nam]
>>> #0/7 [$$$ Bangkok | $$$ P03013220] Wat Ratchabophit Sathitmahasimaram ==> TripAdvisor [Wat Phra Singh]
>>> #0/8 [$$$ Bangkok | $$$ P03013220] Wat Ratchabophit Sathitmahasimaram ==> TripAdvisor [Wat Chaiwatt

In [12]:
tripadvisor_central_attraction_locations = pd.read_csv("dataset/central_tourism_attraction_locations_en.csv")

In [13]:
tripadvisor_central_attraction_locations.drop_duplicates(subset=['location_id'], inplace=True)
tripadvisor_central_attraction_locations

KeyError: Index(['location_id'], dtype='object')

In [14]:
# tripadvisor_central_attraction_locations.to_csv("TripAdvisor_Location_Ids.csv")
tripadvisor_central_attraction_locations = pd.read_csv("dataset/TripAdvisor_Location_Ids.csv")

In [19]:
tripadvisor_central_attraction_locations

Unnamed: 0  location_id  \
0              0      2209612   
1              1      2273363   
2              2       311043   
3              3       317504   
4              4       456322   
...          ...          ...   
1899        6905     13009981   
1900        6906      3256228   
1901        6907      2515972   
1902        6911     13365103   
1903        6912      2645868   

                                                 name         province  \
0                                    Wat Ratchabophit          Bangkok   
1     Wat Rajapradit Sathitmahasimaram Rajaworavihara          Bangkok   
2                                  Wat Phra Chetuphon          Bangkok   
3                           Temple Of Dawn (Wat Arun)          Bangkok   
4                                           Wat Umong          Bangkok   
...                                               ...              ...   
1899                               Thai Sabai Massage  Samut Songkhram   
1900                          Phuket Dragon Muay Thai  Samut Songkhram   
1901                       Thai Cooking School Phuket  Samut Songkhram   
1902                     Nong Bua Thai Dessert Market  Samut Songkhram   
1903                     Free Thai (Seri Thai) Museum  Samut Songkhram   

       place_id  
0     P03013220  
1     P03013220  
2     P03013220  
3     P03013220  
4     P03013220  
...         ...  
1899  P03012297  
1900  P03012297  
1901  P03012297  
1902  P03000251  
1903  P03000251  

[1904 rows x 5 columns]

In [16]:
tripadvisor_central_attraction_locations.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1904 entries, 0 to 1903
Data columns (total 5 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   Unnamed: 0   1904 non-null   int64 
 1   location_id  1904 non-null   int64 
 2   name         1904 non-null   object
 3   province     1904 non-null   object
 4   place_id     1904 non-null   object
dtypes: int64(2), object(3)
memory usage: 74.5+ KB


In [20]:
currentValue = tripadvisor_central_attraction_locations[tripadvisor_central_attraction_locations['location_id'] == 1831068]

currentIndex = currentValue.index[0] + 1
currentIndex

470

In [21]:
valueAfterRecentlyIndex = tripadvisor_central_attraction_locations.loc[currentIndex + 1:]
valueAfterRecentlyIndex

Unnamed: 0  location_id                               name  \
471          841     10598605                Prasat Nakhon Luang   
472          842     15188655   Wat Thep Prasat Sa Kamphaeng Noi   
473          863     10721768                             Wat Ku   
474          864      2660351  Wat Chamthewi Temple (Wat Ku Kut)   
475          865       552544      Wat Ku Tao (Wat Welu Wanaram)   
...          ...          ...                                ...   
1899        6905     13009981                 Thai Sabai Massage   
1900        6906      3256228            Phuket Dragon Muay Thai   
1901        6907      2515972         Thai Cooking School Phuket   
1902        6911     13365103       Nong Bua Thai Dessert Market   
1903        6912      2645868       Free Thai (Seri Thai) Museum   

             province   place_id  
471        Nonthaburi  P03013503  
472        Nonthaburi  P03013503  
473        Nonthaburi  P03013863  
474        Nonthaburi  P03013863  
475        Nonthaburi  P03013863  
...               ...        ...  
1899  Samut Songkhram  P03012297  
1900  Samut Songkhram  P03012297  
1901  Samut Songkhram  P03012297  
1902  Samut Songkhram  P03000251  
1903  Samut Songkhram  P03000251  

[1433 rows x 5 columns]

In [22]:
tripadvisor_reviews = []

for k, location in valueAfterRecentlyIndex.iterrows():
    response = TripAdvisor_api.location_reviews(
        location['location_id'],
        "en"
    )
    
    try:
        reviews = response.json()['data']
        if len(reviews) == 0:
            continue
        
        review = {f"{location['location_id']}": reviews}
        tripadvisor_reviews.append(review)
        
        print(f" #{k + 1} >>> {location['location_id']}")
        
    except KeyError:
        continue
    
    # if (k == 5):
    #     break

 #472 >>> 10598605
 #474 >>> 10721768
 #475 >>> 2660351
 #476 >>> 552544
 #477 >>> 546141
 #478 >>> 12677255
 #479 >>> 6987966
 #480 >>> 8692912
 #481 >>> 8766239
 #482 >>> 12899859
 #483 >>> 8513347
 #484 >>> 23849387
 #485 >>> 4322919
 #486 >>> 24145635
 #487 >>> 7349165
 #488 >>> 4322812
 #489 >>> 9841520
 #490 >>> 7803993
 #491 >>> 7378165
 #492 >>> 555163
 #493 >>> 7893503
 #494 >>> 7085120
 #495 >>> 18970930
 #496 >>> 9465408
 #497 >>> 629586
 #499 >>> 6669473
 #500 >>> 19806689
 #501 >>> 6420132
 #502 >>> 15766163
 #503 >>> 4322774
 #504 >>> 4322426
 #505 >>> 7623381
 #506 >>> 6668953
 #507 >>> 1898000
 #508 >>> 10004680
 #509 >>> 13225651
 #510 >>> 1746798
 #512 >>> 6737314
 #513 >>> 10039369
 #514 >>> 6161636
 #515 >>> 8155426
 #516 >>> 7235354
 #518 >>> 1370390
 #519 >>> 552562
 #520 >>> 4681001
 #521 >>> 12987726
 #522 >>> 553851
 #523 >>> 3668668
 #526 >>> 10533364
 #528 >>> 12945784
 #529 >>> 17379247
 #530 >>> 16731872
 #531 >>> 8874054
 #532 >>> 2161059
 #533 >>> 1204865

KeyboardInterrupt: 

In [23]:
tripadvisor_reviews

[{'10598605': [{'id': 779430404,
    'lang': 'en',
    'location_id': 10598605,
    'published_date': '2020-12-17T06:50:22Z',
    'rating': 5,
    'helpful_votes': 1,
    'rating_image_url': 'https://www.tripadvisor.com/img/cdsi/img2/ratings/traveler/s5.0-66827-5.svg',
    'url': 'https://www.tripadvisor.com/ShowUserReviews-g2238741-d10598605-r779430404-Reviews-Prasat_Nakhon_Luang-Nakhon_Luang_Ayutthaya_Province.html?m=66827#review779430404',
    'text': 'Prasat Nakhon Luang is located some 19km north of Ayutthaya and is truly worth the trip. In fact among all the temples we visited in the privince, this one easily stood out. In addition it is rather quiet and off the beaten track. Do not miss it when visiting Ayutthaya!',
    'title': 'This temple is a Must see!',
    'trip_type': 'Couples',
    'travel_date': '2020-12-31',
    'user': {'username': 'TequilaPepita',
     'user_location': {'id': '293916', 'name': 'Bangkok'},
     'avatar': {'thumbnail': 'https://media-cdn.tripadvisor.co

In [24]:
json_file_path = 'dataset/TripAdvisor_reviews_EN_Set-3.json'
import json

# Open the file in write mode and save the JSON data
with open(json_file_path, 'w') as json_file:
    json.dump(tripadvisor_reviews, json_file, indent=4)

In [18]:
# Initialize an empty list for json_var
json_var = []

# Data to be appended
data = [{"test_1": 3, "test_2": 2}]

# Loop through the range and append data to json_var
for i in range(5):
    json_var.append(data)

# Display the result
print(json_var)


[[{'test_1': 3, 'test_2': 2}], [{'test_1': 3, 'test_2': 2}], [{'test_1': 3, 'test_2': 2}], [{'test_1': 3, 'test_2': 2}], [{'test_1': 3, 'test_2': 2}]]


In [ ]:
# Import necessary libraries
import geopandas as gpd
import matplotlib.pyplot as plt

# Load the GeoJSON file
geojson_file = 'hook/data/thai_province_coordinates_geo.json'
gdf = gpd.read_file(geojson_file)

# Check for empty geometries and remove them
gdf = gdf[~gdf.is_empty]

# Ensure the CRS is set to WGS 84 (EPSG:4326)
if gdf.crs is None:
    gdf.set_crs(epsg=4326, inplace=True)

# Initialize a Matplotlib figure and axis
fig, ax = plt.subplots(figsize=(12, 8))

# Plot all provinces in light blue
gdf.plot(ax=ax, color='lightblue', edgecolor='black')

# Highlight Bangkok in red, checking if it exists in the data
bangkok = gdf[gdf['name'] == 'Bangkok Metropolis']
if not bangkok.empty:
    bangkok.plot(ax=ax, color='red', edgecolor='black')

# Set the aspect of the plot to equal to ensure accurate representation
ax.set_aspect('equal')

# Add title and labels
ax.set_title('Map of Thai Provinces with Bangkok Highlighted', fontsize=15)
ax.set_xlabel('Longitude', fontsize=12)
ax.set_ylabel('Latitude', fontsize=12)

# Show the plot
plt.show()
